<table style="width: 100%; border-style: none">
<tr style="border-style: none; background-color: #82a8cf">
<td style="border-style: none; width: 1%; text-align: left; font-size: 16px; color: #ffffff">Institut f&uuml;r Theoretische Physik<br /> <font color="#e6e6e6">Universit&auml;t zu K&ouml;ln </font></td>
<td style="border-style: none; width: 1%; font-size: 16px">&nbsp;</td>
<td style="border-style: none; width: 1%; text-align: right; font-size: 16px; color: #ffffff">Prof. Dr. Simon Trebst<br /> <font color="#e6e6e6"> Theo Haas </font> </td>
</tr>
</table>
<hr>
<h1 style="font-weight:bold; text-align: center; margin: 10px; padding:0px;">Computerphysik</h1>
<h1 style="font-weight:bold; text-align: center; margin: 0px; padding:0px;">Vorlesung - Programmiertechniken 6</h1>
<hr>
<h3 style="font-weight:bold; text-align: center; margin: 0px; padding:0px; margin-bottom: 20px;">Sommersemester 2025</h3>

**Website:** <a href="https://www.thp.uni-koeln.de/trebst/Lectures/2025-CompPhys.shtml" style="color:#82a8cf; text-decoration: underline;text-decoration-style: dotted;">https://www.thp.uni-koeln.de/trebst/Lectures/2025-CompPhys.shtml</a>

**Themen dieses Notebooks:** Zeitaufgelöste Streuung an einem Potential, "Split-step" Methode, Fourier-Transformationen
<hr>

## Zeitaufgelöste Streuung an einem Potential

Bevor es richtig losgeht, binden wir wie immer einige Pakete ein. Insbesondere nutzen wir das "[FFTW](https://en.wikipedia.org/wiki/FFTW)" Paket zur Berechnung der (diskreten) **Fourier-Transformationen** der Wellenfunktion zwischen Orts- und Impulsraumdarstellung.

In [1]:
# Pakete einbinden
using GLMakie
using LinearAlgebra
using FFTW
GLMakie.activate!(inline = false) # Fenster öffnen

In [2]:
# Hier die Schriftgröße ändern.
mytheme = Theme(fontsize = 50)
set_theme!(mytheme)

Für die Integration der Schrödingergleichung **diskretisieren** wir die Zeitentwicklung in Schritten von $dt$. Auch die Koordinaten in Orts- und im Fourier-transformierten Impulsraum diskretisieren wir, wobei wir wir $N=2^{11}$ diskrete Koordinaten betrachten wollen. 

In [3]:
# Diskretisierungen
# h_bar = m = 1.0 per Definition

dt = 0.01

# Hier den Bereich auf dem die Wellenfunktion definiert ist ändern.
N = 2^12
dx = 0.1
xs = dx .* (collect(1:N) .- 0.5*N)

dk = 2 * pi / (N*dx)
ks = -0.5 * N * dk .+ dk .* collect(1:N);

### Definition des Potentials ###

Im folgenden wollen wir ein Potential definieren, an dem wir das einlaufende Wellenpaket streuen wollen. Dabei betrachten wir **Potentialbarrieren** (positives Potential), **Potentialtöpfe** (negatives Potential), und **Doppelbarrieren** in einem gewissen Abstand. 

In [4]:
# Definition des Potential
function set_potential(V0, V_width, V_distance=0)
    V = zeros(length(xs))
    
    ### single potential
    if(V_distance == 0)
        for i in 1:N
            if( abs(xs[i])<V_width/2 ) V[i] = V0 end
        end
    end
    
    ### two potentials
    if(V_distance != 0)
        for i in 1:N
            if( abs(xs[i])<V_distance/2 + V_width && abs(xs[i])>V_distance/2 ) V[i] = V0 end
        end
    end
        
    return V
end

set_potential (generic function with 2 methods)

### Definition eines einlaufenden Wellenpakets ###

Als erstes wollen wir ein quantenmechanisches Wellenpaket definieren, welches im Ortsraum anfänglich die Form einer **Gauss'schen Glockenkurve** haben soll und sich mit einem Impuls $k_0$ nach rechts (oder links) bewegen soll.

$\quad \quad \psi(x) = \frac{1}{\sqrt{\sigma \cdot \sqrt{\pi}}} \cdot e^{-\frac{\left(x-x_0\right)^2}{2\sigma^2} + \, i \, x \cdot k_0}$



In [5]:
# Definition der Wellenfuntion
function set_wavefunction(k0, x0 = -60)
    # Gaussian
    sigma = 12.0 / k0
    
    # "linkes" Wellenpaket
    psi_x0 = (1/sqrt((sigma * sqrt(pi))) .* exp.(complex.(-0.5.*((xs .- x0)./sigma).^2, xs .* k0)))
    
    # "rechtes" Wellenpaket
    # x1 = 30
    # psi_x1 = (1/sqrt((sigma * sqrt(pi))) .* exp.(complex.(-0.5.*((xs .- x1)./sigma).^2, -xs .* k0)))

    return psi_x0 # + psi_x1
end

set_wavefunction (generic function with 2 methods)

### Halb-Schritt Integration der zeitabhängigen Schrödinger-Gleichung und interaktive Animation ###

Die eigentliche Hauptroutine unseres Programms formuliert das gerade in der Tafelpräsentation eingeführte Halb-Schritt-Verfahren zur Integration der zeitabhängigen Schrödinger-Gleichung. 

Dabei wechseln wir mittel Fourier-Transformation geschickt zwischen Orts- und Impulsraum-Darstellung hin und her, und integrieren jeweils den "einfachen" Teil der Schrödingergleichung.

Schrödingergleichung im **Ortsraum**

$\quad \quad \left(-\frac{\hbar^2}{2m}\frac{\partial^2}{\partial x^2} + V(x) \right)\psi(x,t) = i\hbar \frac{\partial}{\partial t}\psi(x,t)$

Schrödingergleichung im **Impulsraum**

$\quad \quad \left(-\frac{\hbar^2k^2}{2m} + V\left(i \frac{\partial}{\partial k}\right) \right)\tilde\psi(k,t) = i\hbar \frac{\partial}{\partial t}\tilde\psi(k,t)$

In der numerischen Umsetzung der Fourier-Transformation werden wir mit einer *diskreten* Fourier-Transformation arbeiten (eben jenem [FFTW](https://en.wikipedia.org/wiki/FFTW)-Verfahren). Dazu müssen wir die Wellenfunktion in Orts- und Impulsraum in diskreter Form darstellen. Eine gute Einführung hierzu findet sich etwa in diesem [Blog-Post](https://jakevdp.github.io/blog/2012/09/05/quantum-python/) zum hier beschriebenen Halb-Schritt-Verfahren.


### Simulation – Version 2 (controls & update button) ###

Eine etwas schickere Version mit verschiedenen Reglern und Update Botton.

In [6]:
# Version 2 - update on button

# Interactive
using Printf, LaTeXStrings

function create_interactive()
    # Set up GUI
    fig = Figure()
    
    # Potential Controls
    sublayout = fig[1, 1]
    Label(sublayout[1, 1:2], "Potential")
    V0_slider = Slider(sublayout[2, 2], range = -16:0.05:12, startvalue = 1.0)
    Label(sublayout[2, 1], map(v -> latexstring(@sprintf("V_0 = %0.3f", v)), V0_slider.value), halign = :left)
    V_width_slider = Slider(sublayout[3, 2], range = 0:0.2:8, startvalue = 5)
    Label(sublayout[3, 1], map(v -> latexstring("V_\\mathrm{width} = $v"), V_width_slider.value), halign = :left)
    V_distance_slider = Slider(sublayout[4, 2], range = 0:1:80, startvalue = 0.0)
    Label(sublayout[4, 1], map(v -> latexstring("V_\\mathrm{distance} = $v"), V_distance_slider.value), halign = :left)

    # Wavefunction controls
    Label(sublayout[1, 3:4], "Wavefunction")
    x0_slider = Slider(sublayout[2, 4], range = floor(Int64,xs[2]):1:floor(Int64,xs[end]), startvalue = -80)
    Label(sublayout[2, 3], map(v -> latexstring("x_0 = $v"), x0_slider.value), halign = :left)
    k0_slider = Slider(sublayout[3, 4], range = 0:0.05:5, startvalue = 1.5)
    Label(sublayout[3, 3], map(v -> latexstring(@sprintf("k_0 = %0.3f", v)), k0_slider.value), halign = :left)

    # Button
    reset = Button(sublayout[4, 3:4][1, 1], label = "Reset", tellwidth = false)
    paused = Observable(false)
    pause = Button(sublayout[4, 3:4][1, 2], label = map(paused -> paused ? "Resume" : "Pause", paused), tellwidth = false)
    on(trigger -> paused[] = !paused[], pause.clicks)

    # Set up Axis
    ax = Axis(fig[2, 1])
    xlims!(ax, xs[1], xs[end])
    ylims!(ax, -0.03, 0.28)
    
    # Set up starting data
    V   = Observable(set_potential(V0_slider.value[], V_width_slider.value[], V_distance_slider.value[]))
    psi = Observable(set_wavefunction(k0_slider.value[], x0_slider.value[]))

    # Draw Potential, zero line and wavefunction
    band!(ax, xs, zeros(length(xs)), V, color = :lightblue, fxaa = false)
    hlines!(ax, 0.0, color = :black, linewidth = 3)
    lines!(ax, xs, map(vec -> abs2.(vec), psi), color = RGBf(0.333, 0, 0), linewidth = 2)

    # Open the window
    display(fig)

    # discrete Fourier transformation
    psi_mod_x = psi[] .* exp.(complex.(0, -ks[1] .* xs)) .* dx ./ (sqrt(2 * pi))

    # Setup reset
    on(reset.clicks) do _
        V[]   = set_potential(V0_slider.value[], V_width_slider.value[], V_distance_slider.value[])
        psi[] = set_wavefunction(k0_slider.value[], x0_slider.value[])
        copyto!(psi_mod_x, psi[] .* exp.(complex.(0, -ks[1] .* xs)) .* dx ./ (sqrt(2 * pi)))
    end

    ### core iteration (async allows for rendering to occurs during this loop)
    frametime = 1/30
    
    @async while events(fig).window_open[]
        t0 = time()

        if !paused[]
            for _ in 1:4 # updates per shown frames
                # update step
                for j in 1:20
                    psi_mod_x .*= exp.( complex.(0, -0.5*V[]*dt)) 
                    psi_mod_k = fft(psi_mod_x) 
                    psi_mod_k .*= exp.( complex.(0, -0.5 * (ks .* ks) * dt)) 
                    psi_mod_x = ifft(psi_mod_k)  
                    psi_mod_x .*= exp.( complex.(0, -0.5*V[]*dt)) 
                end
                
                # discrete Fourier transformation (avoid update by writing to psi.val)
                psi.val = psi_mod_x .* exp.(complex.(0, ks[1] .* xs)) .* sqrt(2 * pi) / dx
            end

            # update plot 
            notify(psi)
        end

        # delay for plotting
        sleep(max(0, frametime - time() + t0))
    end    

    return 
end

create_interactive (generic function with 1 method)

In [7]:
create_interactive()

### Simulation – Version 3 (controls & immediate update) ###

Eine etwas schickere Version mit verschiedenen Reglern und instantanem Update.

In [8]:
# Version 3 - immediate updates

using Printf, LaTeXStrings

function create_interactive()
    # Set up GUI
    fig = Figure(size = (800,600))
    
    # Potential Controls
    sublayout = fig[1, 1]
    Label(sublayout[1, 1:2], "Potential")
    V0_slider = Slider(sublayout[2, 2], range = -5:0.05:5, startvalue = 1.0)
    Label(sublayout[2, 1], map(v -> latexstring(@sprintf("V_0 = %0.3f", v)), V0_slider.value), halign = :left)
    V_width_slider = Slider(sublayout[3, 2], range = 0:1:80, startvalue = 5)
    Label(sublayout[3, 1], map(v -> latexstring("V_\\mathrm{width} = $v"), V_width_slider.value), halign = :left)
    V_distance_slider = Slider(sublayout[4, 2], range = 0:1:80, startvalue = 0.0)
    Label(sublayout[4, 1], map(v -> latexstring("V_\\mathrm{distance} = $v"), V_distance_slider.value), halign = :left)

    # Wavefunction controls
    Label(sublayout[1, 3:4], "Wavefunction")
    x0_slider = Slider(sublayout[2, 4], range = floor(Int64,xs[2]):1:floor(Int64,xs[end]), startvalue = -80)
    Label(sublayout[2, 3], map(v -> latexstring("x_0 = $v"), x0_slider.value), halign = :left)
    k0_slider = Slider(sublayout[3, 4], range = 0:0.05:5, startvalue = 1.5)
    Label(sublayout[3, 3], map(v -> latexstring(@sprintf("k_0 = %0.3f", v)), k0_slider.value), halign = :left)

    # Button
    reset = Button(sublayout[4, 3:4][1, 1], label = "Reset", tellwidth = false)
    paused = Observable(false)
    pause = Button(sublayout[4, 3:4][1, 2], label = map(paused -> paused ? "Resume" : "Pause", paused), tellwidth = false)
    on(trigger -> paused[] = !paused[], pause.clicks)

    # Set up Axis
    ax = Axis(fig[2, 1])
    xlims!(ax, xs[1], xs[end])
    ylims!(ax, -0.03, 0.28)
    
    # Set up starting data
    V   = map(set_potential, V0_slider.value, V_width_slider.value, V_distance_slider.value)
    psi = map(set_wavefunction, k0_slider.value, x0_slider.value)

    # Draw Potential, zero line and wavefunction
    band!(ax, xs, zeros(length(xs)), V, color = :lightblue, fxaa = false)
    hlines!(ax, 0.0, color = :black, linewidth = 3)
    lines!(ax, xs, map(vec -> abs2.(vec), psi), color = RGBf(0.333, 0, 0), linewidth = 2)

    # Open the window
    display(fig)

    # discrete Fourier transformation
    psi_mod_x = map(psi -> psi .* exp.(complex.(0, -ks[1] .* xs)) .* dx ./ (sqrt(2 * pi)), psi)

    # Setup reset
    on(reset.clicks) do _
        notify(k0_slider.value)
        copyto!(psi_mod_x[], psi[] .* exp.(complex.(0, -ks[1] .* xs)) .* dx ./ (sqrt(2 * pi))) ###########################
    end

    ### core iteration (async allows for rendering to occurs during this loop)
    frametime = 1/30
    
    @async while events(fig).window_open[]
        t0 = time()

        if !paused[]
            for _ in 1:4 # updates per shown frames
                # update step
                for j in 1:20
                    psi_mod_x.val .*= exp.( complex.(0, -0.5*V[]*dt)) 
                    psi_mod_k       = fft(psi_mod_x.val) 
                    psi_mod_k     .*= exp.( complex.(0, -0.5 * (ks .* ks) * dt)) 
                    psi_mod_x.val   = ifft(psi_mod_k)  
                    psi_mod_x.val .*= exp.( complex.(0, -0.5*V[]*dt)) 
                end
                
                # discrete Fourier transformation (avoid update by writing to psi.val)
                psi.val = psi_mod_x.val .* exp.(complex.(0, ks[1] .* xs)) .* sqrt(2 * pi) / dx
            end

            # update plot 
            notify(psi)
        end

        # delay for plotting
        sleep(max(0, frametime - time() + t0))
    end    

    return 
end

create_interactive (generic function with 1 method)

In [9]:
create_interactive()